In [21]:
import pandas as pd
import folium
from folium.plugins import HeatMap
from folium.plugins import MarkerCluster
import geopandas as gp

In [2]:
df_hosp = pd.read_csv('../Data/Cleaned/Hospitals.csv')

In [22]:
df_hosp.head()

Long        Lat     OGF_ID  \
0 -79.369347  43.649813  127907976   
1 -79.384047  43.664337  127907977   
2 -79.377200  43.649990  127907978   
3 -79.364552  43.654664  127907979   
4 -79.375083  43.667650  127907980   

                                        ENGLISH_NAME  \
0               2-Spirited People of the 1st Nations   
1                           Action Positive VIH-SIDA   
2  African and Caribbean Council on HIV/AIDS in O...   
3               Africans in Partnership Against AIDS   
4  AIDS Bereavement & Resiliency Project of Ontar...   

             ADDRESS_LINE_1 ADDRESS_LINE_2 ADDRESS_DESCRIPTOR COMMUNITY  \
0     145 Front Street East       Unit 105  Practice Location   Toronto   
1          543 Yonge Street      4th floor  Practice Location   Toronto   
2        20 Victoria Street      4th floor  Practice Location   Toronto   
3  526 Richmond Street East      2nd Floor  Practice Location   Toronto   
4     490 Sherbourne Street      2nd Floor  Practice Location   Toronto   

  POSTAL_CODE  OBJECTID                    geometry  
0      M5A1E3    753601  POINT (-79.36935 43.64981)  
1      M4Y1Y5    753602  POINT (-79.38405 43.66434)  
2      M5C2N8    753603  POINT (-79.37720 43.64999)  
3      M5A1R3    753604  POINT (-79.36455 43.65466)  
4      M4X1K9    753605  POINT (-79.37508 43.66765)

In [ ]:
df_hosp.ADDRESS_DESCRIPTOR.value_counts()

*convert geometry column in hospital dataset to geo dataframe for easily joining it to neighbourhood gesjson file*  
Both join's need to be in geodata frame

In [3]:
gdp_hosp = gp.GeoDataFrame(df_hosp,
                           geometry = gp.points_from_xy(df_hosp.Long,df_hosp.Lat),
                            crs="EPSG:4326")

In [4]:
df_nei = gp.read_file('../Data/Cleaned/neighbourhoods.geojson')

In [5]:
df_nei.shape

(140, 3)

In [6]:
hjoins = gp.sjoin(gdp_hosp, df_nei, how='right',op='within')

*explore the number of hospitals in a neighbourhood*

In [7]:
hjoins.shape

(2259, 14)

In [8]:
hjoins.neighbourhood.value_counts()

Bay Street Corridor           86
Church-Yonge Corridor         81
Annex                         58
Islington-City Centre West    57
Kensington-Chinatown          54
                              ..
Highland Creek                 1
West Hill                      1
Centennial Scarborough         1
Lambton Baby Point             1
Pelmo Park-Humberlea           1
Name: neighbourhood, Length: 140, dtype: int64

*creating a new table for Number of hospitals in neighbourhood*

In [9]:
df_aggregate = hjoins.groupby(by='neighbourhood').agg({'OGF_ID':'count'}).reset_index().rename(columns={'OGF_ID':'No_of_Hospitals','neighbourhood':'Neighbourhood'})

In [10]:
df_aggregate

Neighbourhood  No_of_Hospitals
0                 Agincourt North                9
1    Agincourt South-Malvern West               28
2                       Alderwood                8
3                           Annex               58
4               Banbury-Don Mills               32
..                            ...              ...
135                      Wychwood               19
136                Yonge-Eglinton               11
137                Yonge-St.Clair                7
138       York University Heights               36
139            Yorkdale-Glen Park               25

[140 rows x 2 columns]

*Initialize map cordinates to toronto & the default map*

In [11]:
df_aggregate = df_aggregate.merge(df_nei,how='inner', left_on='Neighbourhood',right_on='neighbourhood')

In [15]:
df_aggregate = gp.GeoDataFrame(df_aggregate)

In [12]:
df_aggregate.neighbourhood.value_counts()

Wexford/Maryvale       1
Wychwood               1
South Riverdale        1
Yonge-Eglinton         1
Rosedale-Moore Park    1
                      ..
Dufferin Grove         1
Bendale                1
Old East York          1
Long Branch            1
Parkwoods-Donalda      1
Name: neighbourhood, Length: 140, dtype: int64

In [16]:
toronto_coord = [43.702270, -79.366074]

map_ = folium.Map(location=toronto_coord, zoom_start=10)

In [17]:
num_of_hospitals = folium.Choropleth(
                            geo_data=df_aggregate,
                            name='choropleth',
                            data=df_aggregate,
                            columns=['Neighbourhood', 'No_of_Hospitals'],
                            key_on='feature.properties.neighbourhood',
                            fill_color='PuBu',
                            fill_opacity=0.7,
                            line_opacity=0.2,
                            line_color='black',
                            legend_name='Number of Hospitals in a Neighbourhood').add_to(map_)

In [18]:
num_of_hospitals.geojson.add_child(
    #folium.features.GeoJsonTooltip(['neighbourhood'],labels=False)
    folium.features.GeoJsonTooltip(fields=['No_of_Hospitals'],aliases = ['No of Hospitals'],
                                   labels=True,
                                   sticky=False))

In [30]:
map_

In [20]:
map2 = folium.Map(location=toronto_coord, tiles = 'cartodbpositron', zoom_start=11, control_scale=True)

In [28]:
folium.Choropleth(geo_data=df_aggregate,
                            name='choropleth',
                            data=df_aggregate,
                            columns=['Neighbourhood', 'No_of_Hospitals'],
                            key_on='feature.properties.neighbourhood',
                            fill_color='PuBu',
                            fill_opacity=0.7,
                            line_opacity=0.2,
                            line_color='black',
                            legend_name='Number of Hospitals in a Neighbourhood').add_to(map2)

In [24]:
hlocations = df_hosp[['Lat','Long']]
hlocationlist = hlocations.values.tolist()

In [25]:
cluster = MarkerCluster(hlocationlist)

In [26]:
cluster.add_to(map2)

In [29]:
map2